In [1]:
import numpy as np
import pandas as pd
import copy

import torch
from torch.utils.data import TensorDataset, DataLoader
from sklearn.preprocessing import MinMaxScaler

from data import fetch_dataset
from util import move_sliding_window, num_params

from model import LSTMModel
from algorithm import cadis

pd.set_option('display.max_columns', None)
pd.set_option('display.max_columns', None)
np.set_printoptions(suppress=True, floatmode='fixed')

In [2]:
if torch.cuda.is_available():
    device = torch.device("cuda")
    print('running on gpu')
else:
    device = torch.device("cpu")

running on gpu


# Parameters

In [3]:
window_size = 90 # Define window_size period and split inputs/labels\
batch_size = 1024
label_col_index = 0

# seq_len = 90  # (timestamps)
hidden_dim = 50
n_layers = 2
lr = 0.0001
output_dim = 1

#fed train params
num_local_epochs = 1
max_rounds = 100 #nb of total rounds for training


# Data Preperation

In [18]:
dataframes = fetch_dataset("./heterog")

Floor0
Floor1
Floor10
Floor11
Floor12
Floor13
Floor14
Floor15
Floor16
Floor17
Floor18
Floor19
Floor2
Floor20
Floor21
Floor22
Floor23
Floor24
Floor25
Floor26
Floor27
Floor28
Floor29
Floor3
Floor30
Floor31
Floor32
Floor33
Floor34
Floor35
Floor36
Floor37
Floor38
Floor39
Floor4
Floor40
Floor41
Floor42
Floor43
Floor44
Floor45
Floor46
Floor47
Floor48
Floor49
Floor5
Floor50
Floor51
Floor52
Floor53
Floor54
Floor55
Floor56
Floor57
Floor58
Floor59
Floor6
Floor60
Floor61
Floor62
Floor63
Floor64
Floor65
Floor66
Floor67
Floor68
Floor69
Floor7
Floor70
Floor71
Floor72
Floor73
Floor74
Floor75
Floor76
Floor77
Floor78
Floor79
Floor8
Floor80
Floor81
Floor82
Floor83
Floor84
Floor85
Floor86
Floor87
Floor88
Floor89
Floor9


In [19]:
n_clients = len(dataframes) #total number of clients to partition data into

In [20]:
for _, df in dataframes.items():
    print(df.columns)
    print(df.shape)

Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(68183, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(58618, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(46840, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(65390, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(57176, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(51707, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
      dtype='object')
(47453, 9)
Index(['total_demand', 'AC', 'Light', 'Plug', 'Year', 'Month', 'Day', 'Hour',
       'Minute'],
 

# Build the training set

In [21]:
train_loader = []
test_loader = []
label_scalers = []
for _, df in dataframes.items():
    inputs_cols_indices = range(0, df.shape[1])  # use (total_demand,Year,Month,Day,Hour,Minute) columns as features
    #move the window
    inputs, labels = move_sliding_window(
        df.values,
        window_size,
        inputs_cols_indices=inputs_cols_indices,
        label_col_index=label_col_index
    )

    # Normalize the input data columns
    sc = MinMaxScaler()
    # Obtaining the scaler for the labels(usage data) so that output can be re-scaled to actual value during evaluation
    label_sc = MinMaxScaler()

    # Split data into train/test portions and combining all data into a single array
    test_portion = int(0.2 * len(inputs))

    train_x = sc.fit_transform(inputs[:-test_portion].reshape(-1, window_size * df.shape[1]))
    train_x = train_x.reshape(-1, window_size, df.shape[1])
    train_y = label_sc.fit_transform(labels[:-test_portion])

    test_x = sc.transform(inputs[-test_portion:].reshape(-1, window_size * df.shape[1]))
    test_x = test_x.reshape(-1, window_size, df.shape[1])
    test_y = label_sc.transform(labels[-test_portion:])

    # test_x.append(testx)
    # test_y.append(testy)
    label_scalers.append(label_sc)

    # pytorch data loaders
    train_data = TensorDataset(torch.from_numpy(train_x).to('cpu'), torch.from_numpy(train_y).to('cpu'))
    train_loader.append(DataLoader(train_data, batch_size=batch_size, drop_last=True))# Drop the last incomplete batch
    test_data = TensorDataset(torch.from_numpy(test_x).to('cpu'), torch.from_numpy(test_y).to('cpu'))
    test_loader.append(DataLoader(test_data, batch_size=batch_size))# Drop the last incomplete batch

    # release some memory
    del train_x, train_y
input_dim = next(iter(train_loader[0]))[0].shape[2]  # 22

(68093, 90, 9) (68093, 1)
(58528, 90, 9) (58528, 1)
(46750, 90, 9) (46750, 1)
(65300, 90, 9) (65300, 1)
(57086, 90, 9) (57086, 1)
(51617, 90, 9) (51617, 1)
(47363, 90, 9) (47363, 1)
(68901, 90, 9) (68901, 1)
(67168, 90, 9) (67168, 1)
(69578, 90, 9) (69578, 1)
(62003, 90, 9) (62003, 1)
(49050, 90, 9) (49050, 1)
(61853, 90, 9) (61853, 1)
(69521, 90, 9) (69521, 1)
(67302, 90, 9) (67302, 1)
(72217, 90, 9) (72217, 1)
(46055, 90, 9) (46055, 1)
(57157, 90, 9) (57157, 1)
(64807, 90, 9) (64807, 1)
(66845, 90, 9) (66845, 1)
(61800, 90, 9) (61800, 1)
(55024, 90, 9) (55024, 1)
(65910, 90, 9) (65910, 1)
(49996, 90, 9) (49996, 1)
(63049, 90, 9) (63049, 1)
(64836, 90, 9) (64836, 1)
(64007, 90, 9) (64007, 1)
(69858, 90, 9) (69858, 1)
(56491, 90, 9) (56491, 1)
(65359, 90, 9) (65359, 1)
(61733, 90, 9) (61733, 1)
(66320, 90, 9) (66320, 1)
(61236, 90, 9) (61236, 1)
(71305, 90, 9) (71305, 1)
(52888, 90, 9) (52888, 1)
(58160, 90, 9) (58160, 1)
(70972, 90, 9) (70972, 1)
(61987, 90, 9) (61987, 1)
(43972, 90, 

# LSTM model

In [22]:
lstm = LSTMModel(input_dim, hidden_dim, output_dim, n_layers)
model_type = 'LSTM'
print(lstm)
print(num_params(lstm))

LSTMModel(
  (lstm): LSTM(9, 50, num_layers=2, batch_first=True)
  (fc): Linear(in_features=50, out_features=1, bias=True)
  (tanh): Tanh()
)
32651


# Fedcadis

## 10

In [9]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [0 1 2 3 4 5 6 7 8 9]
round 0, starting client 1/10, id: 0
Epoch [1/1], Loss: 3.2016
round 0, starting client 2/10, id: 1
Epoch [1/1], Loss: 2.2772
round 0, starting client 3/10, id: 2
Epoch [1/1], Loss: 1.6033
round 0, starting client 4/10, id: 3
Epoch [1/1], Loss: 1.1736
round 0, starting client 5/10, id: 4
Epoch [1/1], Loss: 2.0271
round 0, starting client 6/10, id: 5
Epoch [1/1], Loss: 1.9743
round 0, starting client 7/10, id: 6
Epoch [1/1], Loss: 2.1860
round 0, starting client 8/10, id: 7
Epoch [1/1], Loss: 2.3795
round 0, starting client 9/10, id: 8
Epoch [1/1], Loss: 2.0580
round 0, starting client 10/10, id: 9
Epoch [1/1], Loss: 2.3275


C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 59.77336602108901%
MAE: 14.173248121608474
RMSE: 20.376773581316712
Average Loss:  0.04770855866887386

starting avg round 1
clients:  [0 1 2 3 4 5 6 7 8 9]
round 1, starting client 1/10, id: 0
Epoch [1/1], Loss: 2.7936
round 1, starting client 2/10, id: 1
Epoch [1/1], Loss: 2.0000
round 1, starting client 3/10, id: 2
Epoch [1/1], Loss: 1.5095
round 1, starting client 4/10, id: 3
Epoch [1/1], Loss: 1.1596
round 1, starting client 5/10, id: 4
Epoch [1/1], Loss: 1.8035
round 1, starting client 6/10, id: 5
Epoch [1/1], Loss: 1.6887
round 1, starting client 7/10, id: 6
Epoch [1/1], Loss: 1.9584
round 1, starting client 8/10, id: 7
Epoch [1/1], Loss: 2.1571
round 1, starting client 9/10, id: 8
Epoch [1/1], Loss: 1.8004
round 1, starting client 10/10, id: 9
Epoch [1/1], Loss: 2.0543


C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 59.09675214343625%
MAE: 13.92968994420872
RMSE: 19.362334669191206
Average Loss:  0.04341055414004429

starting avg round 2
clients:  [0 1 2 3 4 5 6 7 8 9]
round 2, starting client 1/10, id: 0
Epoch [1/1], Loss: 2.4159
round 2, starting client 2/10, id: 1
Epoch [1/1], Loss: 1.7422
round 2, starting client 3/10, id: 2
Epoch [1/1], Loss: 1.3651
round 2, starting client 4/10, id: 3
Epoch [1/1], Loss: 1.1181
round 2, starting client 5/10, id: 4
Epoch [1/1], Loss: 1.5831
round 2, starting client 6/10, id: 5
Epoch [1/1], Loss: 1.4605
round 2, starting client 7/10, id: 6
Epoch [1/1], Loss: 1.7125
round 2, starting client 8/10, id: 7
Epoch [1/1], Loss: 1.8999
round 2, starting client 9/10, id: 8
Epoch [1/1], Loss: 1.5730
round 2, starting client 10/10, id: 9
Epoch [1/1], Loss: 1.7874


...

calc smape: 25.00180545122875%
MAE: 1.926452249756047
RMSE: 4.390679410782831
Average Loss:  0.002439106326803652

starting avg round 98
clients:  [0 1 2 3 4 5 6 7 8 9]
round 98, starting client 1/10, id: 0
Epoch [1/1], Loss: 0.0964
round 98, starting client 2/10, id: 1
Epoch [1/1], Loss: 0.0860
round 98, starting client 3/10, id: 2
Epoch [1/1], Loss: 0.1030
round 98, starting client 4/10, id: 3
Epoch [1/1], Loss: 0.1196
round 98, starting client 5/10, id: 4
Epoch [1/1], Loss: 0.0749
round 98, starting client 6/10, id: 5
Epoch [1/1], Loss: 0.0701
round 98, starting client 7/10, id: 6
Epoch [1/1], Loss: 0.1016
round 98, starting client 8/10, id: 7
Epoch [1/1], Loss: 0.1235
round 98, starting client 9/10, id: 8
Epoch [1/1], Loss: 0.0723
round 98, starting client 10/10, id: 9
Epoch [1/1], Loss: 0.0954


C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 24.856035269880483%
MAE: 1.9272026866265977
RMSE: 4.38147007187502
Average Loss:  0.0024302866580237165

starting avg round 99
clients:  [0 1 2 3 4 5 6 7 8 9]
round 99, starting client 1/10, id: 0
Epoch [1/1], Loss: 0.0961
round 99, starting client 2/10, id: 1
Epoch [1/1], Loss: 0.0855
round 99, starting client 3/10, id: 2
Epoch [1/1], Loss: 0.1027
round 99, starting client 4/10, id: 3
Epoch [1/1], Loss: 0.1195
round 99, starting client 5/10, id: 4
Epoch [1/1], Loss: 0.0745
round 99, starting client 6/10, id: 5
Epoch [1/1], Loss: 0.0697
round 99, starting client 7/10, id: 6
Epoch [1/1], Loss: 0.1010
round 99, starting client 8/10, id: 7
Epoch [1/1], Loss: 0.1230
round 99, starting client 9/10, id: 8
Epoch [1/1], Loss: 0.0721
round 99, starting client 10/10, id: 9
Epoch [1/1], Loss: 0.0950


C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 24.77670299112214%
MAE: 1.927586864623244
RMSE: 4.372247054410479
Average Loss:  0.0024217040639927983
CPU times: total: 26min 46s
Wall time: 26min 52s


In [11]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 20

In [9]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting avg round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 0, starting client 1/20, id: 0
Epoch [1/1], Loss: 5.3126
round 0, starting client 2/20, id: 1
Epoch [1/1], Loss: 3.9873
round 0, starting client 3/20, id: 2
Epoch [1/1], Loss: 2.7167
round 0, starting client 4/20, id: 3
Epoch [1/1], Loss: 3.9557
round 0, starting client 5/20, id: 4
Epoch [1/1], Loss: 4.1431
round 0, starting client 6/20, id: 5
Epoch [1/1], Loss: 3.3370
round 0, starting client 7/20, id: 6
Epoch [1/1], Loss: 3.7656
round 0, starting client 8/20, id: 7
Epoch [1/1], Loss: 4.5316
round 0, starting client 9/20, id: 8
Epoch [1/1], Loss: 4.4050
round 0, starting client 10/20, id: 9
Epoch [1/1], Loss: 4.0769
round 0, starting client 11/20, id: 10
Epoch [1/1], Loss: 4.8399
round 0, starting client 12/20, id: 11
Epoch [1/1], Loss: 2.5781
round 0, starting client 13/20, id: 12
Epoch [1/1], Loss: 2.6439
round 0, starting client 14/20, id: 13
Epoch [1/1], Loss: 1.9290
round 0, starti

C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 58.067641460825136%
MAE: 12.142088941761603
RMSE: 22.94164879102034
Average Loss:  0.06920854045557515

starting avg round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 1, starting client 1/20, id: 0
Epoch [1/1], Loss: 3.6176
round 1, starting client 2/20, id: 1
Epoch [1/1], Loss: 2.5921
round 1, starting client 3/20, id: 2
Epoch [1/1], Loss: 1.7673
round 1, starting client 4/20, id: 3
Epoch [1/1], Loss: 2.7200
round 1, starting client 5/20, id: 4
Epoch [1/1], Loss: 2.7267
round 1, starting client 6/20, id: 5
Epoch [1/1], Loss: 2.2106
round 1, starting client 7/20, id: 6
Epoch [1/1], Loss: 2.5129
round 1, starting client 8/20, id: 7
Epoch [1/1], Loss: 2.8866
round 1, starting client 9/20, id: 8
Epoch [1/1], Loss: 3.0051
round 1, starting client 10/20, id: 9
Epoch [1/1], Loss: 2.6484
round 1, starting client 11/20, id: 10
Epoch [1/1], Loss: 3.2725
round 1, starting client 12/20, id: 11
Epoch [1/1], Loss: 1.6304
round 1, starting client 13/20

C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 58.56848163696505%
MAE: 13.313685975401457
RMSE: 19.359338021798447
Average Loss:  0.049361336060552916

starting avg round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 2, starting client 1/20, id: 0
Epoch [1/1], Loss: 2.7257
round 2, starting client 2/20, id: 1
Epoch [1/1], Loss: 1.9265
round 2, starting client 3/20, id: 2
Epoch [1/1], Loss: 1.4053
round 2, starting client 4/20, id: 3
Epoch [1/1], Loss: 2.1963
round 2, starting client 5/20, id: 4
Epoch [1/1], Loss: 2.0164
round 2, starting client 6/20, id: 5
Epoch [1/1], Loss: 1.6927
round 2, starting client 7/20, id: 6
Epoch [1/1], Loss: 1.8270
round 2, starting client 8/20, id: 7
Epoch [1/1], Loss: 2.1220
round 2, starting client 9/20, id: 8
Epoch [1/1], Loss: 2.3594
round 2, starting client 10/20, id: 9
Epoch [1/1], Loss: 2.0096
round 2, starting client 11/20, id: 10
Epoch [1/1], Loss: 2.4799
round 2, starting client 12/20, id: 11
Epoch [1/1], Loss: 1.2450
round 2, starting client 13/2

...

calc smape: 27.060503217297217%
MAE: 1.8888024951197662
RMSE: 4.1862321367317525
Average Loss:  0.002464451906982831

starting avg round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 98, starting client 1/20, id: 0
Epoch [1/1], Loss: 0.0987
round 98, starting client 2/20, id: 1
Epoch [1/1], Loss: 0.0846
round 98, starting client 3/20, id: 2
Epoch [1/1], Loss: 0.0770
round 98, starting client 4/20, id: 3
Epoch [1/1], Loss: 0.1149
round 98, starting client 5/20, id: 4
Epoch [1/1], Loss: 0.0877
round 98, starting client 6/20, id: 5
Epoch [1/1], Loss: 0.0786
round 98, starting client 7/20, id: 6
Epoch [1/1], Loss: 0.0710
round 98, starting client 8/20, id: 7
Epoch [1/1], Loss: 0.0791
round 98, starting client 9/20, id: 8
Epoch [1/1], Loss: 0.1290
round 98, starting client 10/20, id: 9
Epoch [1/1], Loss: 0.0994
round 98, starting client 11/20, id: 10
Epoch [1/1], Loss: 0.1041
round 98, starting client 12/20, id: 11
Epoch [1/1], Loss: 0.0733
round 98, start

C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 26.870812374881197%
MAE: 1.8893973730883287
RMSE: 4.175847440139428
Average Loss:  0.0024525663500960795

starting avg round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19]
round 99, starting client 1/20, id: 0
Epoch [1/1], Loss: 0.0982
round 99, starting client 2/20, id: 1
Epoch [1/1], Loss: 0.0841
round 99, starting client 3/20, id: 2
Epoch [1/1], Loss: 0.0767
round 99, starting client 4/20, id: 3
Epoch [1/1], Loss: 0.1144
round 99, starting client 5/20, id: 4
Epoch [1/1], Loss: 0.0871
round 99, starting client 6/20, id: 5
Epoch [1/1], Loss: 0.0781
round 99, starting client 7/20, id: 6
Epoch [1/1], Loss: 0.0706
round 99, starting client 8/20, id: 7
Epoch [1/1], Loss: 0.0787
round 99, starting client 9/20, id: 8
Epoch [1/1], Loss: 0.1281
round 99, starting client 10/20, id: 9
Epoch [1/1], Loss: 0.0988
round 99, starting client 11/20, id: 10
Epoch [1/1], Loss: 0.1036
round 99, starting client 12/20, id: 11
Epoch [1/1], Loss: 0.0729
round 99, start

C:\Users\User\Desktop\KD-FL\util.py:151: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 26.571697902472597%
MAE: 1.889918248628685
RMSE: 4.166089375534668
Average Loss:  0.0024407510743885185
CPU times: total: 57min 35s
Wall time: 1h 1min 10s


In [10]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 30 

In [9]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 0, starting client 1/30, id: 0
Epoch [1/1], Loss: 3.2740
round 0, starting client 2/30, id: 1
Epoch [1/1], Loss: 2.3066
round 0, starting client 3/30, id: 2
Epoch [1/1], Loss: 1.5834
round 0, starting client 4/30, id: 3
Epoch [1/1], Loss: 2.5166
round 0, starting client 5/30, id: 4
Epoch [1/1], Loss: 2.4319
round 0, starting client 6/30, id: 5
Epoch [1/1], Loss: 1.9774
round 0, starting client 7/30, id: 6
Epoch [1/1], Loss: 2.2116
round 0, starting client 8/30, id: 7
Epoch [1/1], Loss: 2.5692
round 0, starting client 9/30, id: 8
Epoch [1/1], Loss: 2.7665
round 0, starting client 10/30, id: 9
Epoch [1/1], Loss: 2.3735
round 0, starting client 11/30, id: 10
Epoch [1/1], Loss: 2.9587
round 0, starting client 12/30, id: 11
Epoch [1/1], Loss: 1.4451
round 0, starting client 13/30, id: 12
Epoch [1/1], Loss: 1.5930
round 0, starting client 14/30, id: 13
Epoch [1/1], L

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 57.515080643668846%
MAE: 14.132293132940298
RMSE: 20.880725816513063
Average Loss:  0.05223626277483668

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 1, starting client 1/30, id: 0
Epoch [1/1], Loss: 2.7157
round 1, starting client 2/30, id: 1
Epoch [1/1], Loss: 1.9318
round 1, starting client 3/30, id: 2
Epoch [1/1], Loss: 1.4110
round 1, starting client 4/30, id: 3
Epoch [1/1], Loss: 2.2207
round 1, starting client 5/30, id: 4
Epoch [1/1], Loss: 2.0212
round 1, starting client 6/30, id: 5
Epoch [1/1], Loss: 1.7008
round 1, starting client 7/30, id: 6
Epoch [1/1], Loss: 1.8288
round 1, starting client 8/30, id: 7
Epoch [1/1], Loss: 2.1059
round 1, starting client 9/30, id: 8
Epoch [1/1], Loss: 2.3797
round 1, starting client 10/30, id: 9
Epoch [1/1], Loss: 1.9944
round 1, starting client 11/30, id: 10
Epoch [1/1], Loss: 2.4783
round 1, starting client 12/30, id: 11
Epoch [1/1], Loss: 1.2553
ro

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 56.97047469484619%
MAE: 14.152238256121889
RMSE: 19.436591332485893
Average Loss:  0.04528006635572506

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 2, starting client 1/30, id: 0
Epoch [1/1], Loss: 2.1943
round 2, starting client 2/30, id: 1
Epoch [1/1], Loss: 1.5901
round 2, starting client 3/30, id: 2
Epoch [1/1], Loss: 1.2487
round 2, starting client 4/30, id: 3
Epoch [1/1], Loss: 1.8821
round 2, starting client 5/30, id: 4
Epoch [1/1], Loss: 1.6510
round 2, starting client 6/30, id: 5
Epoch [1/1], Loss: 1.4281
round 2, starting client 7/30, id: 6
Epoch [1/1], Loss: 1.5036
round 2, starting client 8/30, id: 7
Epoch [1/1], Loss: 1.6952
round 2, starting client 9/30, id: 8
Epoch [1/1], Loss: 1.9727
round 2, starting client 10/30, id: 9
Epoch [1/1], Loss: 1.5989
round 2, starting client 11/30, id: 10
Epoch [1/1], Loss: 2.0410
round 2, starting client 12/30, id: 11
Epoch [1/1], Loss: 1.0572
rou

...

calc smape: 22.21720386167536%
MAE: 2.160375553915647
RMSE: 4.686761668029135
Average Loss:  0.004278211734993224

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 98, starting client 1/30, id: 0
Epoch [1/1], Loss: 0.0938
round 98, starting client 2/30, id: 1
Epoch [1/1], Loss: 0.0855
round 98, starting client 3/30, id: 2
Epoch [1/1], Loss: 0.0812
round 98, starting client 4/30, id: 3
Epoch [1/1], Loss: 0.1141
round 98, starting client 5/30, id: 4
Epoch [1/1], Loss: 0.0886
round 98, starting client 6/30, id: 5
Epoch [1/1], Loss: 0.0793
round 98, starting client 7/30, id: 6
Epoch [1/1], Loss: 0.0696
round 98, starting client 8/30, id: 7
Epoch [1/1], Loss: 0.0785
round 98, starting client 9/30, id: 8
Epoch [1/1], Loss: 0.1330
round 98, starting client 10/30, id: 9
Epoch [1/1], Loss: 0.1020
round 98, starting client 11/30, id: 10
Epoch [1/1], Loss: 0.1042
round 98, starting client 12/30, id: 11
Epoch [1/1], Loss

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.267695597434226%
MAE: 2.15603961521486
RMSE: 4.671716797002525
Average Loss:  0.0042725568121734355

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29]
round 99, starting client 1/30, id: 0
Epoch [1/1], Loss: 0.0933
round 99, starting client 2/30, id: 1
Epoch [1/1], Loss: 0.0851
round 99, starting client 3/30, id: 2
Epoch [1/1], Loss: 0.0808
round 99, starting client 4/30, id: 3
Epoch [1/1], Loss: 0.1136
round 99, starting client 5/30, id: 4
Epoch [1/1], Loss: 0.0881
round 99, starting client 6/30, id: 5
Epoch [1/1], Loss: 0.0788
round 99, starting client 7/30, id: 6
Epoch [1/1], Loss: 0.0692
round 99, starting client 8/30, id: 7
Epoch [1/1], Loss: 0.0781
round 99, starting client 9/30, id: 8
Epoch [1/1], Loss: 0.1323
round 99, starting client 10/30, id: 9
Epoch [1/1], Loss: 0.1015
round 99, starting client 11/30, id: 10
Epoch [1/1], Loss: 0.1037
round 99, starting client 12/30, id: 11
Epoch [1/1], Los

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.307680610378952%
MAE: 2.155867392724039
RMSE: 4.660051336951497
Average Loss:  0.004266526349333894
CPU times: total: 3h 10min 54s
Wall time: 3h 33min 15s


In [10]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 40

In [9]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 0, starting client 1/40, id: 0
Epoch [1/1], Loss: 5.1330
round 0, starting client 2/40, id: 1
Epoch [1/1], Loss: 3.8401
round 0, starting client 3/40, id: 2
Epoch [1/1], Loss: 2.6185
round 0, starting client 4/40, id: 3
Epoch [1/1], Loss: 3.8200
round 0, starting client 5/40, id: 4
Epoch [1/1], Loss: 3.9892
round 0, starting client 6/40, id: 5
Epoch [1/1], Loss: 3.2157
round 0, starting client 7/40, id: 6
Epoch [1/1], Loss: 3.6553
round 0, starting client 8/40, id: 7
Epoch [1/1], Loss: 4.3286
round 0, starting client 9/40, id: 8
Epoch [1/1], Loss: 4.2707
round 0, starting client 10/40, id: 9
Epoch [1/1], Loss: 3.8792
round 0, starting client 11/40, id: 10
Epoch [1/1], Loss: 4.6767
round 0, starting client 12/40, id: 11
Epoch [1/1], Loss: 2.4876
round 0, starting client 13/40, id: 12
Epoch [1/1], Loss: 2.5291
round 0, starting clien

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 55.20687977366745%
MAE: 12.36056327878309
RMSE: 23.75733677941521
Average Loss:  0.06893303234205335

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 1, starting client 1/40, id: 0
Epoch [1/1], Loss: 3.3511
round 1, starting client 2/40, id: 1
Epoch [1/1], Loss: 2.3832
round 1, starting client 3/40, id: 2
Epoch [1/1], Loss: 1.6255
round 1, starting client 4/40, id: 3
Epoch [1/1], Loss: 2.5463
round 1, starting client 5/40, id: 4
Epoch [1/1], Loss: 2.5082
round 1, starting client 6/40, id: 5
Epoch [1/1], Loss: 2.0367
round 1, starting client 7/40, id: 6
Epoch [1/1], Loss: 2.3117
round 1, starting client 8/40, id: 7
Epoch [1/1], Loss: 2.6178
round 1, starting client 9/40, id: 8
Epoch [1/1], Loss: 2.8434
round 1, starting client 10/40, id: 9
Epoch [1/1], Loss: 2.4271
round 1, starting client 11/40, id: 10
Epoch [1/1], Loss: 3.0393
round 1, starting client 12/40, id: 11
E

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 57.88614327579806%
MAE: 14.221838981793397
RMSE: 20.151426342866237
Average Loss:  0.04917679848963902

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 2, starting client 1/40, id: 0
Epoch [1/1], Loss: 2.5714
round 2, starting client 2/40, id: 1
Epoch [1/1], Loss: 1.8402
round 2, starting client 3/40, id: 2
Epoch [1/1], Loss: 1.3375
round 2, starting client 4/40, id: 3
Epoch [1/1], Loss: 2.1222
round 2, starting client 5/40, id: 4
Epoch [1/1], Loss: 1.9219
round 2, starting client 6/40, id: 5
Epoch [1/1], Loss: 1.6216
round 2, starting client 7/40, id: 6
Epoch [1/1], Loss: 1.7375
round 2, starting client 8/40, id: 7
Epoch [1/1], Loss: 1.9779
round 2, starting client 9/40, id: 8
Epoch [1/1], Loss: 2.3070
round 2, starting client 10/40, id: 9
Epoch [1/1], Loss: 1.8742
round 2, starting client 11/40, id: 10
Epoch [1/1], Loss: 2.3670
round 2, starting client 12/40, id: 11

...

calc smape: 21.930550217963518%
MAE: 1.9900534365602132
RMSE: 4.17795663080541
Average Loss:  0.0034203883976900266

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 98, starting client 1/40, id: 0
Epoch [1/1], Loss: 0.0810
round 98, starting client 2/40, id: 1
Epoch [1/1], Loss: 0.0733
round 98, starting client 3/40, id: 2
Epoch [1/1], Loss: 0.0726
round 98, starting client 4/40, id: 3
Epoch [1/1], Loss: 0.0961
round 98, starting client 5/40, id: 4
Epoch [1/1], Loss: 0.0745
round 98, starting client 6/40, id: 5
Epoch [1/1], Loss: 0.0673
round 98, starting client 7/40, id: 6
Epoch [1/1], Loss: 0.0597
round 98, starting client 8/40, id: 7
Epoch [1/1], Loss: 0.0643
round 98, starting client 9/40, id: 8
Epoch [1/1], Loss: 0.1117
round 98, starting client 10/40, id: 9
Epoch [1/1], Loss: 0.0848
round 98, starting client 11/40, id: 10
Epoch [1/1], Loss: 0.0881
round 98, starting client

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 21.974426819870626%
MAE: 1.9897973022210051
RMSE: 4.167243052009853
Average Loss:  0.0034143560991603053

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39]
round 99, starting client 1/40, id: 0
Epoch [1/1], Loss: 0.0806
round 99, starting client 2/40, id: 1
Epoch [1/1], Loss: 0.0728
round 99, starting client 3/40, id: 2
Epoch [1/1], Loss: 0.0723
round 99, starting client 4/40, id: 3
Epoch [1/1], Loss: 0.0954
round 99, starting client 5/40, id: 4
Epoch [1/1], Loss: 0.0740
round 99, starting client 6/40, id: 5
Epoch [1/1], Loss: 0.0668
round 99, starting client 7/40, id: 6
Epoch [1/1], Loss: 0.0592
round 99, starting client 8/40, id: 7
Epoch [1/1], Loss: 0.0639
round 99, starting client 9/40, id: 8
Epoch [1/1], Loss: 0.1109
round 99, starting client 10/40, id: 9
Epoch [1/1], Loss: 0.0843
round 99, starting client 11/40, id: 10
Epoch [1/1], Loss: 0.0875
round 99, starting clien

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.014933415646194%
MAE: 1.9896666228031523
RMSE: 4.156058417249786
Average Loss:  0.0034081318731428076
CPU times: total: 2h 56min 21s
Wall time: 4h 4min 18s


In [10]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 50

In [16]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 0, starting client 1/50, id: 0
Epoch [1/1], Loss: 4.2617
round 0, starting client 2/50, id: 1
Epoch [1/1], Loss: 3.1493
round 0, starting client 3/50, id: 2
Epoch [1/1], Loss: 2.1594
round 0, starting client 4/50, id: 3
Epoch [1/1], Loss: 3.1628
round 0, starting client 5/50, id: 4
Epoch [1/1], Loss: 3.2966
round 0, starting client 6/50, id: 5
Epoch [1/1], Loss: 2.6680
round 0, starting client 7/50, id: 6
Epoch [1/1], Loss: 3.0355
round 0, starting client 8/50, id: 7
Epoch [1/1], Loss: 3.4984
round 0, starting client 9/50, id: 8
Epoch [1/1], Loss: 3.5537
round 0, starting client 10/50, id: 9
Epoch [1/1], Loss: 3.1713
round 0, starting client 11/50, id: 10
Epoch [1/1], Loss: 3.8922
round 0, starting client 12/50, id: 11
Epoch [1/1], Loss: 2.0148
round 0, starting client 13/50, id: 12
Epoch [1/1], Loss:

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 56.02311207309751%
MAE: 12.612830801135583
RMSE: 21.001431565793933
Average Loss:  0.05457596955618758

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 1, starting client 1/50, id: 0
Epoch [1/1], Loss: 2.8871
round 1, starting client 2/50, id: 1
Epoch [1/1], Loss: 2.0534
round 1, starting client 3/50, id: 2
Epoch [1/1], Loss: 1.4462
round 1, starting client 4/50, id: 3
Epoch [1/1], Loss: 2.2966
round 1, starting client 5/50, id: 4
Epoch [1/1], Loss: 2.1500
round 1, starting client 6/50, id: 5
Epoch [1/1], Loss: 1.7921
round 1, starting client 7/50, id: 6
Epoch [1/1], Loss: 1.9584
round 1, starting client 8/50, id: 7
Epoch [1/1], Loss: 2.2342
round 1, starting client 9/50, id: 8
Epoch [1/1], Loss: 2.5146
round 1, starting client 10/50, id: 9
Epoch [1/1], Loss: 2.1395
round 1, starting client 11/50, id: 10
Epoch [1/1], Loss: 2.6177
round 1

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 57.7596150132718%
MAE: 14.326140813130893
RMSE: 19.075534885847446
Average Loss:  0.0445090147049033

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 2, starting client 1/50, id: 0
Epoch [1/1], Loss: 2.3412
round 2, starting client 2/50, id: 1
Epoch [1/1], Loss: 1.7147
round 2, starting client 3/50, id: 2
Epoch [1/1], Loss: 1.2863
round 2, starting client 4/50, id: 3
Epoch [1/1], Loss: 1.9933
round 2, starting client 5/50, id: 4
Epoch [1/1], Loss: 1.7670
round 2, starting client 6/50, id: 5
Epoch [1/1], Loss: 1.5239
round 2, starting client 7/50, id: 6
Epoch [1/1], Loss: 1.6077
round 2, starting client 8/50, id: 7
Epoch [1/1], Loss: 1.8229
round 2, starting client 9/50, id: 8
Epoch [1/1], Loss: 2.1204
round 2, starting client 10/50, id: 9
Epoch [1/1], Loss: 1.7403
round 2, starting client 11/50, id: 10
Epoch [1/1], Loss: 2.1684
round 2, 

...

calc smape: 22.90454573417714%
MAE: 1.9214030697745792
RMSE: 4.266250752945135
Average Loss:  0.0032142289572350663

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 98, starting client 1/50, id: 0
Epoch [1/1], Loss: 0.0897
round 98, starting client 2/50, id: 1
Epoch [1/1], Loss: 0.0787
round 98, starting client 3/50, id: 2
Epoch [1/1], Loss: 0.0778
round 98, starting client 4/50, id: 3
Epoch [1/1], Loss: 0.1103
round 98, starting client 5/50, id: 4
Epoch [1/1], Loss: 0.0813
round 98, starting client 6/50, id: 5
Epoch [1/1], Loss: 0.0734
round 98, starting client 7/50, id: 6
Epoch [1/1], Loss: 0.0648
round 98, starting client 8/50, id: 7
Epoch [1/1], Loss: 0.0708
round 98, starting client 9/50, id: 8
Epoch [1/1], Loss: 0.1212
round 98, starting client 10/50, id: 9
Epoch [1/1], Loss: 0.0931
round 98, starting client 11/50, id: 10
Epoch [1/1], Loss: 0

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.895581923826427%
MAE: 1.9203182792595923
RMSE: 4.259490874117795
Average Loss:  0.0032097073310720344

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49]
round 99, starting client 1/50, id: 0
Epoch [1/1], Loss: 0.0894
round 99, starting client 2/50, id: 1
Epoch [1/1], Loss: 0.0784
round 99, starting client 3/50, id: 2
Epoch [1/1], Loss: 0.0777
round 99, starting client 4/50, id: 3
Epoch [1/1], Loss: 0.1100
round 99, starting client 5/50, id: 4
Epoch [1/1], Loss: 0.0810
round 99, starting client 6/50, id: 5
Epoch [1/1], Loss: 0.0731
round 99, starting client 7/50, id: 6
Epoch [1/1], Loss: 0.0647
round 99, starting client 8/50, id: 7
Epoch [1/1], Loss: 0.0706
round 99, starting client 9/50, id: 8
Epoch [1/1], Loss: 0.1208
round 99, starting client 10/50, id: 9
Epoch [1/1], Loss: 0.0928
round 99, starting client 11/50, id: 10
Epoch [1/1], Loss: 

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.871196848449742%
MAE: 1.9196444156885013
RMSE: 4.253129971988231
Average Loss:  0.0032047840859375397
CPU times: total: 3h 14min 10s
Wall time: 5h 3min 45s


In [17]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 60

In [ ]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 0, starting client 1/60, id: 0
Epoch [1/1], Loss: 4.8249
round 0, starting client 2/60, id: 1
Epoch [1/1], Loss: 3.5976
round 0, starting client 3/60, id: 2
Epoch [1/1], Loss: 2.4660
round 0, starting client 4/60, id: 3
Epoch [1/1], Loss: 3.5796
round 0, starting client 5/60, id: 4
Epoch [1/1], Loss: 3.7544
round 0, starting client 6/60, id: 5
Epoch [1/1], Loss: 3.0293
round 0, starting client 7/60, id: 6
Epoch [1/1], Loss: 3.4345
round 0, starting client 8/60, id: 7
Epoch [1/1], Loss: 4.0419
round 0, starting client 9/60, id: 8
Epoch [1/1], Loss: 4.0061
round 0, starting client 10/60, id: 9
Epoch [1/1], Loss: 3.6480
round 0, starting client 11/60, id: 10
Epoch [1/1], Loss: 4.4105
round 0, starting client 12/60, id: 11
Epoch [1/1], Loss: 2.3100
round 0, starting client 13

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 56.41396612069103%
MAE: 12.192039080148286
RMSE: 22.12877945905818
Average Loss:  0.06354528890425866

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 1, starting client 1/60, id: 0
Epoch [1/1], Loss: 3.2306
round 1, starting client 2/60, id: 1
Epoch [1/1], Loss: 2.2981
round 1, starting client 3/60, id: 2
Epoch [1/1], Loss: 1.5861
round 1, starting client 4/60, id: 3
Epoch [1/1], Loss: 2.4971
round 1, starting client 5/60, id: 4
Epoch [1/1], Loss: 2.4151
round 1, starting client 6/60, id: 5
Epoch [1/1], Loss: 1.9799
round 1, starting client 7/60, id: 6
Epoch [1/1], Loss: 2.2083
round 1, starting client 8/60, id: 7
Epoch [1/1], Loss: 2.5289
round 1, starting client 9/60, id: 8
Epoch [1/1], Loss: 2.7611
round 1, starting client 10/60, id: 9
Epoch [1/1], Loss: 2.3800
round 1, starting client 11/60, id: 10
Epoc

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 57.81835385979528%
MAE: 13.98280467775777
RMSE: 19.451648802561966
Average Loss:  0.04841845467972248

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 2, starting client 1/60, id: 0
Epoch [1/1], Loss: 2.5919
round 2, starting client 2/60, id: 1
Epoch [1/1], Loss: 1.8794
round 2, starting client 3/60, id: 2
Epoch [1/1], Loss: 1.3699
round 2, starting client 4/60, id: 3
Epoch [1/1], Loss: 2.1514
round 2, starting client 5/60, id: 4
Epoch [1/1], Loss: 1.9473
round 2, starting client 6/60, id: 5
Epoch [1/1], Loss: 1.6520
round 2, starting client 7/60, id: 6
Epoch [1/1], Loss: 1.7653
round 2, starting client 8/60, id: 7
Epoch [1/1], Loss: 2.0190
round 2, starting client 9/60, id: 8
Epoch [1/1], Loss: 2.3158
round 2, starting client 10/60, id: 9
Epoch [1/1], Loss: 1.9274
round 2, starting client 11/60, id: 10
Epoc

...

calc smape: 21.448458892728553%
MAE: 1.9044782155558697
RMSE: 4.452713299307449
Average Loss:  0.002983780317442237

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 98, starting client 1/60, id: 0
Epoch [1/1], Loss: 0.1032
round 98, starting client 2/60, id: 1
Epoch [1/1], Loss: 0.0914
round 98, starting client 3/60, id: 2
Epoch [1/1], Loss: 0.0843
round 98, starting client 4/60, id: 3
Epoch [1/1], Loss: 0.1267
round 98, starting client 5/60, id: 4
Epoch [1/1], Loss: 0.0950
round 98, starting client 6/60, id: 5
Epoch [1/1], Loss: 0.0858
round 98, starting client 7/60, id: 6
Epoch [1/1], Loss: 0.0746
round 98, starting client 8/60, id: 7
Epoch [1/1], Loss: 0.0801
round 98, starting client 9/60, id: 8
Epoch [1/1], Loss: 0.1400
round 98, starting client 10/60, id: 9
Epoch [1/1], Loss: 0.1077
round 98, starting client 11/6

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 21.379857896010886%
MAE: 1.9033129732992364
RMSE: 4.445213488250374
Average Loss:  0.002976557980457771

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59]
round 99, starting client 1/60, id: 0
Epoch [1/1], Loss: 0.1028
round 99, starting client 2/60, id: 1
Epoch [1/1], Loss: 0.0910
round 99, starting client 3/60, id: 2
Epoch [1/1], Loss: 0.0841
round 99, starting client 4/60, id: 3
Epoch [1/1], Loss: 0.1262
round 99, starting client 5/60, id: 4
Epoch [1/1], Loss: 0.0945
round 99, starting client 6/60, id: 5
Epoch [1/1], Loss: 0.0854
round 99, starting client 7/60, id: 6
Epoch [1/1], Loss: 0.0742
round 99, starting client 8/60, id: 7
Epoch [1/1], Loss: 0.0799
round 99, starting client 9/60, id: 8
Epoch [1/1], Loss: 0.1394
round 99, starting client 10/60, id: 9
Epoch [1/1], Loss: 0.1072
round 99, starting client 11/6

C:\Users\User\Desktop\KD-FL\util.py:132: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 21.309968742479874%
MAE: 1.9022817814431798
RMSE: 4.4374710981161405
Average Loss:  0.0029694232516368343
CPU times: total: 4h 10s
Wall time: 6h 27min 37s


In [ ]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 70

In [9]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 0, starting client 1/70, id: 0
Epoch [1/1], Loss: 6.8640
round 0, starting client 2/70, id: 1
Epoch [1/1], Loss: 5.2865
round 0, starting client 3/70, id: 2
Epoch [1/1], Loss: 3.6770
round 0, starting client 4/70, id: 3
Epoch [1/1], Loss: 5.2270
round 0, starting client 5/70, id: 4
Epoch [1/1], Loss: 5.4366
round 0, starting client 6/70, id: 5
Epoch [1/1], Loss: 4.4416
round 0, starting client 7/70, id: 6
Epoch [1/1], Loss: 4.9241
round 0, starting client 8/70, id: 7
Epoch [1/1], Loss: 6.0289
round 0, starting client 9/70, id: 8
Epoch [1/1], Loss: 5.7682
round 0, starting client 10/70, id: 9
Epoch [1/1], Loss: 5.4433
round 0, starting client 11/70, id: 10
Epoch [1/1], Loss: 6.2542
round 0, starting client 12/70, id: 11
Epoch [1/1], Loss: 3.56

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 99.99999966625191%
MAE: 15.295861286014743
RMSE: 26.77219545537564
Average Loss:  0.09033887957635432

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 1, starting client 1/70, id: 0
Epoch [1/1], Loss: 4.0400
round 1, starting client 2/70, id: 1
Epoch [1/1], Loss: 2.9413
round 1, starting client 3/70, id: 2
Epoch [1/1], Loss: 2.0115
round 1, starting client 4/70, id: 3
Epoch [1/1], Loss: 3.0031
round 1, starting client 5/70, id: 4
Epoch [1/1], Loss: 3.0843
round 1, starting client 6/70, id: 5
Epoch [1/1], Loss: 2.5099
round 1, starting client 7/70, id: 6
Epoch [1/1], Loss: 2.8753
round 1, starting client 8/70, id: 7
Epoch [1/1], Loss: 3.2610
round 1, starting client 9/70, id: 8
Epoch [1/1], Loss: 3.3418
round 1, starting client 10/70, id: 9
Epoch [1/1], Loss: 2.9437
round 1, star

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 56.07869413778037%
MAE: 12.818843986324408
RMSE: 20.102760517274806
Average Loss:  0.05041756372536009

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 2, starting client 1/70, id: 0
Epoch [1/1], Loss: 2.6072
round 2, starting client 2/70, id: 1
Epoch [1/1], Loss: 1.8314
round 2, starting client 3/70, id: 2
Epoch [1/1], Loss: 1.3501
round 2, starting client 4/70, id: 3
Epoch [1/1], Loss: 2.1135
round 2, starting client 5/70, id: 4
Epoch [1/1], Loss: 1.9212
round 2, starting client 6/70, id: 5
Epoch [1/1], Loss: 1.6265
round 2, starting client 7/70, id: 6
Epoch [1/1], Loss: 1.7521
round 2, starting client 8/70, id: 7
Epoch [1/1], Loss: 2.0048
round 2, starting client 9/70, id: 8
Epoch [1/1], Loss: 2.2693
round 2, starting client 10/70, id: 9
Epoch [1/1], Loss: 1.8817
round 2, sta

...

calc smape: 20.615197330255533%
MAE: 1.8760225979115324
RMSE: 4.277960075940587
Average Loss:  0.002703233948640164

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 98, starting client 1/70, id: 0
Epoch [1/1], Loss: 0.0976
round 98, starting client 2/70, id: 1
Epoch [1/1], Loss: 0.0815
round 98, starting client 3/70, id: 2
Epoch [1/1], Loss: 0.0718
round 98, starting client 4/70, id: 3
Epoch [1/1], Loss: 0.1124
round 98, starting client 5/70, id: 4
Epoch [1/1], Loss: 0.0846
round 98, starting client 6/70, id: 5
Epoch [1/1], Loss: 0.0758
round 98, starting client 7/70, id: 6
Epoch [1/1], Loss: 0.0677
round 98, starting client 8/70, id: 7
Epoch [1/1], Loss: 0.0759
round 98, starting client 9/70, id: 8
Epoch [1/1], Loss: 0.1257
round 98, starting client 10/70, id: 9
Epoch [1/1], Loss: 0.0973


C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 20.62472817852949%
MAE: 1.8717508383585375
RMSE: 4.26796238606875
Average Loss:  0.0026951840184936287

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69]
round 99, starting client 1/70, id: 0
Epoch [1/1], Loss: 0.0971
round 99, starting client 2/70, id: 1
Epoch [1/1], Loss: 0.0812
round 99, starting client 3/70, id: 2
Epoch [1/1], Loss: 0.0715
round 99, starting client 4/70, id: 3
Epoch [1/1], Loss: 0.1119
round 99, starting client 5/70, id: 4
Epoch [1/1], Loss: 0.0842
round 99, starting client 6/70, id: 5
Epoch [1/1], Loss: 0.0754
round 99, starting client 7/70, id: 6
Epoch [1/1], Loss: 0.0673
round 99, starting client 8/70, id: 7
Epoch [1/1], Loss: 0.0756
round 99, starting client 9/70, id: 8
Epoch [1/1], Loss: 0.1251
round 99, starting client 10/70, id: 9
Epoch [1/1], Loss: 0.0969
r

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 20.617834992461912%
MAE: 1.8691804377924361
RMSE: 4.259181785308167
Average Loss:  0.002687347099498069
CPU times: total: 4h 17min 36s
Wall time: 6h 33s


In [10]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 80

In [ ]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 0, starting client 1/80, id: 0
Epoch [1/1], Loss: 5.3308
round 0, starting client 2/80, id: 1
Epoch [1/1], Loss: 4.0047
round 0, starting client 3/80, id: 2
Epoch [1/1], Loss: 2.7362
round 0, starting client 4/80, id: 3
Epoch [1/1], Loss: 3.9808
round 0, starting client 5/80, id: 4
Epoch [1/1], Loss: 4.1551
round 0, starting client 6/80, id: 5
Epoch [1/1], Loss: 3.3498
round 0, starting client 7/80, id: 6
Epoch [1/1], Loss: 3.7869
round 0, starting client 8/80, id: 7
Epoch [1/1], Loss: 4.5444
round 0, starting client 9/80, id: 8
Epoch [1/1], Loss: 4.4408
round 0, starting client 10/80, id: 9
Epoch [1/1], Loss: 4.0834
round 0, starting client 11/80, id: 10
Epoch [1/1], Loss: 4.8603
round 0, starting client 12/80,

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 57.19420799039801%
MAE: 11.911245923037606
RMSE: 23.369968290449215
Average Loss:  0.07509172691702769

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 1, starting client 1/80, id: 0
Epoch [1/1], Loss: 3.4556
round 1, starting client 2/80, id: 1
Epoch [1/1], Loss: 2.4805
round 1, starting client 3/80, id: 2
Epoch [1/1], Loss: 1.6961
round 1, starting client 4/80, id: 3
Epoch [1/1], Loss: 2.5993
round 1, starting client 5/80, id: 4
Epoch [1/1], Loss: 2.6101
round 1, starting client 6/80, id: 5
Epoch [1/1], Loss: 2.1192
round 1, starting client 7/80, id: 6
Epoch [1/1], Loss: 2.4216
round 1, starting client 8/80, id: 7
Epoch [1/1], Loss: 2.7391
round 1, starting client 9/80, id: 8
Epoch [1/1], Loss: 2.8925
round 1, starting client 10/80, id: 9
Epoch [

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 55.579572500136294%
MAE: 12.465996122546109
RMSE: 18.85294877064937
Average Loss:  0.04824141967786996

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 2, starting client 1/80, id: 0
Epoch [1/1], Loss: 2.3757
round 2, starting client 2/80, id: 1
Epoch [1/1], Loss: 1.6880
round 2, starting client 3/80, id: 2
Epoch [1/1], Loss: 1.2526
round 2, starting client 4/80, id: 3
Epoch [1/1], Loss: 1.9494
round 2, starting client 5/80, id: 4
Epoch [1/1], Loss: 1.7694
round 2, starting client 6/80, id: 5
Epoch [1/1], Loss: 1.5004
round 2, starting client 7/80, id: 6
Epoch [1/1], Loss: 1.6078
round 2, starting client 8/80, id: 7
Epoch [1/1], Loss: 1.8248
round 2, starting client 9/80, id: 8
Epoch [1/1], Loss: 2.1084
round 2, starting client 10/80, id: 9
Epoch [

...

calc smape: 22.93982880108453%
MAE: 2.0924332792880014
RMSE: 4.378047532798702
Average Loss:  0.003700692049262661

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 98, starting client 1/80, id: 0
Epoch [1/1], Loss: 0.0899
round 98, starting client 2/80, id: 1
Epoch [1/1], Loss: 0.0772
round 98, starting client 3/80, id: 2
Epoch [1/1], Loss: 0.0709
round 98, starting client 4/80, id: 3
Epoch [1/1], Loss: 0.1057
round 98, starting client 5/80, id: 4
Epoch [1/1], Loss: 0.0807
round 98, starting client 6/80, id: 5
Epoch [1/1], Loss: 0.0713
round 98, starting client 7/80, id: 6
Epoch [1/1], Loss: 0.0626
round 98, starting client 8/80, id: 7
Epoch [1/1], Loss: 0.0713
round 98, starting client 9/80, id: 8
Epoch [1/1], Loss: 0.1204
round 98, starting client 10/80, id

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.781364204232595%
MAE: 2.0863517610734585
RMSE: 4.366638447428875
Average Loss:  0.0036957171518448685

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79]
round 99, starting client 1/80, id: 0
Epoch [1/1], Loss: 0.0895
round 99, starting client 2/80, id: 1
Epoch [1/1], Loss: 0.0770
round 99, starting client 3/80, id: 2
Epoch [1/1], Loss: 0.0704
round 99, starting client 4/80, id: 3
Epoch [1/1], Loss: 0.1049
round 99, starting client 5/80, id: 4
Epoch [1/1], Loss: 0.0797
round 99, starting client 6/80, id: 5
Epoch [1/1], Loss: 0.0708
round 99, starting client 7/80, id: 6
Epoch [1/1], Loss: 0.0622
round 99, starting client 8/80, id: 7
Epoch [1/1], Loss: 0.0709
round 99, starting client 9/80, id: 8
Epoch [1/1], Loss: 0.1196
round 99, starting client 10/80, 

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 22.593774720593665%
MAE: 2.0832191683653027
RMSE: 4.359524384077699
Average Loss:  0.0036910396275938264
CPU times: total: 5h 10min 37s
Wall time: 7h 49min 58s


In [ ]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)

## 90

In [23]:
%%time
lstm_K5_cadis = copy.deepcopy(lstm)
outputs_cadis, targets_cadis, loss_cadis, smape_cadis, mae_cadis, rmse_cadis = cadis(
    global_model = lstm_K5_cadis,
    client_train_loader = train_loader,
    test_loader = test_loader,
    lambda_kd = 1,
    label_sc = label_scalers,
    n_clients = n_clients,
    batch_size = batch_size,
    num_local_epochs = num_local_epochs,
    lr = lr,
    max_rounds = max_rounds,
    model_type = model_type,
    device = device,
)


starting round 0
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 0, starting client 1/90, id: 0
Epoch [1/1], Loss: 3.1554
round 0, starting client 2/90, id: 1
Epoch [1/1], Loss: 2.2288
round 0, starting client 3/90, id: 2
Epoch [1/1], Loss: 1.5578
round 0, starting client 4/90, id: 3
Epoch [1/1], Loss: 2.4883
round 0, starting client 5/90, id: 4
Epoch [1/1], Loss: 2.3440
round 0, starting client 6/90, id: 5
Epoch [1/1], Loss: 1.9320
round 0, starting client 7/90, id: 6
Epoch [1/1], Loss: 2.1168
round 0, starting client 8/90, id: 7
Epoch [1/1], Loss: 2.4625
round 0, starting client 9/90, id: 8
Epoch [1/1], Loss: 2.7153
round 0, starting client 10/90, id: 9
Epoch [1/1], Loss: 2.3190
round 0, starting client 11/90, id: 10
Epoch [1/1], Loss: 2.8637
r

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 57.437350067184106%
MAE: 13.75564072697144
RMSE: 19.685676683073332
Average Loss:  0.05342375166451314

starting round 1
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 1, starting client 1/90, id: 0
Epoch [1/1], Loss: 2.7715
round 1, starting client 2/90, id: 1
Epoch [1/1], Loss: 1.9797
round 1, starting client 3/90, id: 2
Epoch [1/1], Loss: 1.4427
round 1, starting client 4/90, id: 3
Epoch [1/1], Loss: 2.2771
round 1, starting client 5/90, id: 4
Epoch [1/1], Loss: 2.0781
round 1, starting client 6/90, id: 5
Epoch [1/1], Loss: 1.7390
round 1, starting client 7/90, id: 6
Epoch [1/1], Loss: 1.8721
round 1, starting client 8/90, id: 7
Epoch [1/1], Loss: 2.1611
round 1, starting client 9/90, id: 8
Epoch [1/1], Loss: 2.4529
round 1, starti

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 56.296024076471795%
MAE: 13.246465029936848
RMSE: 18.567327331211565
Average Loss:  0.047598200321067374

starting round 2
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 2, starting client 1/90, id: 0
Epoch [1/1], Loss: 2.3293
round 2, starting client 2/90, id: 1
Epoch [1/1], Loss: 1.6768
round 2, starting client 3/90, id: 2
Epoch [1/1], Loss: 1.2784
round 2, starting client 4/90, id: 3
Epoch [1/1], Loss: 1.9640
round 2, starting client 5/90, id: 4
Epoch [1/1], Loss: 1.7579
round 2, starting client 6/90, id: 5
Epoch [1/1], Loss: 1.4919
round 2, starting client 7/90, id: 6
Epoch [1/1], Loss: 1.5937
round 2, starting client 8/90, id: 7
Epoch [1/1], Loss: 1.8022
round 2, starting client 9/90, id: 8
Epoch [1/1], Loss: 2.1029
round 2, star

...

calc smape: 21.85209505494356%
MAE: 2.0020861839772026
RMSE: 4.4269693595135
Average Loss:  0.003174107833936735

starting round 98
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 98, starting client 1/90, id: 0
Epoch [1/1], Loss: 0.0975
round 98, starting client 2/90, id: 1
Epoch [1/1], Loss: 0.0866
round 98, starting client 3/90, id: 2
Epoch [1/1], Loss: 0.0842
round 98, starting client 4/90, id: 3
Epoch [1/1], Loss: 0.1196
round 98, starting client 5/90, id: 4
Epoch [1/1], Loss: 0.0909
round 98, starting client 6/90, id: 5
Epoch [1/1], Loss: 0.0820
round 98, starting client 7/90, id: 6
Epoch [1/1], Loss: 0.0725
round 98, starting client 8/90, id: 7
Epoch [1/1], Loss: 0.0769
round 98, starting client 9/90, id: 8
Epoch [1/1], Loss: 0.1344
round 9

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 21.860106634263115%
MAE: 2.000225703569362
RMSE: 4.419189508758248
Average Loss:  0.003164993291255894

starting round 99
clients:  [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89]
round 99, starting client 1/90, id: 0
Epoch [1/1], Loss: 0.0971
round 99, starting client 2/90, id: 1
Epoch [1/1], Loss: 0.0863
round 99, starting client 3/90, id: 2
Epoch [1/1], Loss: 0.0841
round 99, starting client 4/90, id: 3
Epoch [1/1], Loss: 0.1192
round 99, starting client 5/90, id: 4
Epoch [1/1], Loss: 0.0905
round 99, starting client 6/90, id: 5
Epoch [1/1], Loss: 0.0817
round 99, starting client 7/90, id: 6
Epoch [1/1], Loss: 0.0724
round 99, starting client 8/90, id: 7
Epoch [1/1], Loss: 0.0767
round 99, starting client 9/90, id: 8
Epoch [1/1], Loss: 0.1339
round

C:\Users\User\Desktop\KD-FL\util.py:149: ClusterWarning: scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  linkage_matrix = linkage(q_matrix, method='average')


calc smape: 21.867238439460177%
MAE: 1.999124686952874
RMSE: 4.4123669784038775
Average Loss:  0.003156596650097965
CPU times: total: 5h 53min 57s
Wall time: 9h 5min 5s


In [24]:
np.save(f'metrics/cadis_outputs_C{n_clients}.npy', np.array(outputs_cadis, dtype=object))
np.save(f'metrics/cadis_targets_C{n_clients}.npy', np.array(targets_cadis, dtype=object))
np.save(f'metrics/cadis_loss_C{n_clients}.npy', loss_cadis)
np.save(f'metrics/cadis_smape_C{n_clients}.npy', smape_cadis)
np.save(f'metrics/cadis_mae_C{n_clients}.npy', mae_cadis)
np.save(f'metrics/cadis_rmse_C{n_clients}.npy', rmse_cadis)